# Prospect of new restaurant business in London

## Introduction

### 1. Business Problem

Restaurant business is thriving in London due to its diverse culture and London being a hotspot for tourism. Being a Londoner, I have experienced the trouble of finding cuisines of choice in certain part of the cities, leaving me wonder the flourishing business prospect of a restaurant in those areas. However rather than going with guess work on the location, this project is make use of Machine learning and the data available online to analyse the hotspots for new restaurant locations/cuisines.

###  2. Data

information about London boroughs and locations from https://en.wikipedia.org/wiki/List_of_areas_of_London. <br>
Use the Geopy and Folium library to get the coordinates of every locations and map geospatial data on a London map.<br>
Using Foursquare API, collect the top 100 restaurants and their categories for each location within a radius 500 meters.


### 3. Methodology

#### Install the packages required for Analysis

In [1]:
!conda install -c conda-forge wikipedia --yes
!conda install -c conda-forge folium=0.5.0 --yes
!conda install -c conda-forge geopy --yes
!conda install -c conda-forge geocoder --yes

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - wikipedia


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    wikipedia-1.4.0            |             py_2          13 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.4 MB

The following NEW packages will be INSTALLED:

    python_abi:      3.6-1_cp36m       conda-forge
    wikipedia:       1.4.0-py_2        conda-forge

The following packages will be UPDATED:

   

#### Importing the packages required for Analysis

Before we get the data and start exploring it, let's import dependencies that we will need.

In [2]:
#Importing the packages required for Analysis
import requests
import pandas as pd
import numpy as np
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import wikipedia as wp
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter 

Python Wikipedia library is used to scrape the data from wikipedia page <a href="https://en.wikipedia.org/wiki/List_of_areas_of_London">click here</a> this holds the  neighborhood and borough informations. <br><br>
For our analysis, we are only interested in the location with Post Town='LONDON'

In [190]:
html = wp.page("List of areas of London").html().encode("UTF-8")
df_rawdata = pd.read_html(html)[1]
df=df_rawdata[df_rawdata['Post town'] =='LONDON']
df.head()

Location                     London borough Post town Postcode district  \
0  Abbey Wood              Bexley, Greenwich [7]    LONDON               SE2   
1       Acton  Ealing, Hammersmith and Fulham[8]    LONDON            W3, W4   
6     Aldgate                           City[10]    LONDON               EC3   
7     Aldwych                    Westminster[10]    LONDON               WC2   
9     Anerley                        Bromley[11]    LONDON              SE20   

  Dial code OS grid ref  
0       020    TQ465785  
1       020    TQ205805  
6       020    TQ334813  
7       020    TQ307810  
9       020    TQ345695

In [191]:
#Check how the dataset looks like 
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 299 entries, 0 to 530
Data columns (total 6 columns):
Location             299 non-null object
London borough       299 non-null object
Post town            299 non-null object
Postcode district    299 non-null object
Dial code            299 non-null object
OS grid ref          299 non-null object
dtypes: object(6)
memory usage: 16.4+ KB


In [193]:
#Assigning column names and cleaning the data of borough columns to remove the []
df.columns = ['Location','London_borough','Post town','Postcode district','Dial Code','OS grid ref']
df['London_borough'] =  df['London_borough'].apply(lambda x: x.replace('[','').replace(']','')) 
df['London_borough'] =  df['London_borough'].str.replace('\d+', '')
df['London_borough'] =  df['London_borough'].str.split(',').str[0]

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pa

In [194]:
#Drop the columns irrelevent for the analysis and adding new two columns to store latitude and longitude
df.drop(['Postcode district','Dial Code','OS grid ref'],axis=1, inplace=True)
df['Latitude']=0
df['Longitude']=0

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/ind

In [197]:
#Analyse the records in the dataset and the size of the data
df.head()

Location London_borough Post town  Latitude  Longitude
0  Abbey Wood         Bexley    LONDON         0          0
1       Acton         Ealing    LONDON         0          0
6     Aldgate           City    LONDON         0          0
7     Aldwych    Westminster    LONDON         0          0
9     Anerley        Bromley    LONDON         0          0

In [198]:
#Check the size of the data
df.shape

(299, 5)

#### Convert an address into latitude and longitude values  - Using geocoder

In [199]:
import geocoder # import geocoder
latitude = []
longitude = []
for i in range(len(df)):
    address = ','.join(map(str,list(df.iloc[i, :3])))    
    geolocator = Nominatim(user_agent="london_explorer")
    geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)
    location = geolocator.geocode(address)
    try: 
        latitude.append(location.latitude)
        longitude.append(location.longitude)
    except:
        latitude.append("Not Found")
        longitude.append("Not Found")
    
print('Done!')

Done!


In [202]:
#Assign the value of Longitude and latitude to the dataframe
df['Latitude']=latitude
df['Longitude']=longitude

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()


In [203]:
#View the dataset
df.head()

Location London_borough Post town Latitude  Longitude
0  Abbey Wood         Bexley    LONDON    51.49   0.132891
1       Acton         Ealing    LONDON  51.5081  -0.273261
6     Aldgate           City    LONDON  51.5142 -0.0757186
7     Aldwych    Westminster    LONDON  51.5131  -0.117593
9     Anerley        Bromley    LONDON  51.4076 -0.0619394

In [204]:
#Dropping the index 
df.reset_index(drop=True, inplace=True)

In [205]:
df.head(5)

Location London_borough Post town Latitude  Longitude
0  Abbey Wood         Bexley    LONDON    51.49   0.132891
1       Acton         Ealing    LONDON  51.5081  -0.273261
2     Aldgate           City    LONDON  51.5142 -0.0757186
3     Aldwych    Westminster    LONDON  51.5131  -0.117593
4     Anerley        Bromley    LONDON  51.4076 -0.0619394

In [206]:
# Write into CSV - Backing up the data
df.to_pickle('London.csv')
df.to_csv('LondonRestaurant.csv')

In [209]:
#Records with co-oridnates are assigned to a new dataframe this will now be used for further analysis
df_london=df[df["Latitude"]!="Not Found"]

In [210]:
df_london.head()

Location London_borough Post town Latitude  Longitude
0  Abbey Wood         Bexley    LONDON    51.49   0.132891
1       Acton         Ealing    LONDON  51.5081  -0.273261
2     Aldgate           City    LONDON  51.5142 -0.0757186
3     Aldwych    Westminster    LONDON  51.5131  -0.117593
4     Anerley        Bromley    LONDON  51.4076 -0.0619394

In [18]:
df_london.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 293 entries, 0 to 298
Data columns (total 5 columns):
Location          293 non-null object
London_borough    293 non-null object
Post town         293 non-null object
Latitude          293 non-null object
Longitude         293 non-null object
dtypes: object(5)
memory usage: 13.7+ KB


In [19]:
df_london.drop_duplicates(inplace=True)

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [21]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df_london['London_borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 32 boroughs and 299 neighborhoods.


#### Get the London "central" point


In [212]:
address = 'London, England'

geolocator = Nominatim(user_agent="london_explorer")
location = geolocator.geocode(address)
lat_e = location.latitude
long_e = location.longitude
print('The geograpical coordinate of London City are {}, {}.'.format(lat_e, long_e))

The geograpical coordinate of London City are 51.5073219, -0.1276474.


#### create map of London using starting point coordinates

In [213]:
import folium
map_london = folium.Map(location=[lat_e, long_e], zoom_start=10)

# add markers to map
for lat, lng, borough, location in zip(df_london['Latitude'], df_london['Longitude'], df_london['London_borough'], df_london['Location']):
    label = '{}, {}'.format(location, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

We have explored the london boroughs and locations using the scraped data from wikipedia page. Lets now look at the restaurant informations of these locations using Foursquare API to explore the neighborhoods and segment them

#### Exploring London Restaurants using Foursquare API

Setting the Foursquare Credentials and Version

In [24]:
LIMIT = 200
CLIENT_ID = 'PAMLV50THNC031WTGXMUEAD5CEQRWVPT4UC2VZ12XHIXBRQW' # your Foursquare ID
CLIENT_SECRET = 'L5YPYTJIIFV5TDSRIT34S1PFALUB2TS0M0SU221UITY2UWBV' # your Foursquare Secret
VERSION = '20191116' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: PAMLV50THNC031WTGXMUEAD5CEQRWVPT4UC2VZ12XHIXBRQW
CLIENT_SECRET:L5YPYTJIIFV5TDSRIT34S1PFALUB2TS0M0SU221UITY2UWBV


Creating a new dataframe with Venue information recieved from Foursquare API using co-ordinates  . Venue Type - restaurants

In [70]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&query=restaurant'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        #results = requests.get(url).json()["response"]['groups'][0]['items']
        results = requests.get(url).json()['response'].get('groups',[{}])[0].get('items', [])
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list],columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category'])
    """nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']"""
    return(nearby_venues)
                             

Above function is invoked on each neighborhood and create a new dataframe called London_venues

In [71]:
London_venues = getNearbyVenues(names=df['Location'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )


Abbey Wood
Acton
Aldgate
Aldwych
Anerley
Angel
Archway
Arnos Grove
Balham
Bankside
Barbican
Barnes
Barnsbury
Battersea
Bayswater
Bedford Park
Belgravia
Bellingham
Belsize Park
Bermondsey
Bethnal Green
Blackfriars
Blackheath
Blackheath Royal Standard
Blackwall
Bloomsbury
Bounds Green
Bow
Bowes Park
Brent Cross
Brent Park
Brixton
Brockley
Bromley (also Bromley-by-Bow)
Brompton
Brondesbury
Brunswick Park
Burroughs, The
Camberwell
Cambridge Heath
Camden Town
Canary Wharf
Cann Hall
Canning Town
Canonbury
Castelnau
Catford
Chalk Farm
Charing Cross
Charlton
Chelsea
Childs Hill
Chinatown
Chinbrook
Chingford
Chiswick
Church End
Church End
Clapham
Clerkenwell
Colindale
Colliers Wood
Colney Hatch
Covent Garden
Cricklewood
Crofton Park
Crossness
Crouch End
Crystal Palace
Cubitt Town
Custom House
Dalston
Dartford
De Beauvoir Town
Denmark Hill
Deptford
Dollis Hill
Dulwich
Ealing
Earls Court
Earlsfield
East Dulwich
East Finchley
East Ham
East Sheen
Edmonton
Elephant and Castle
Eltham
Farringdon
Finch

Checking the size of the resulting dataframe

In [214]:
print(London_venues.shape)

(6188, 7)


In [215]:
London_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   Abbey Wood              51.489962                0.132891   
1        Acton              51.508140               -0.273261   
2        Acton              51.508140               -0.273261   
3        Acton              51.508140               -0.273261   
4        Acton              51.508140               -0.273261   

                    Venue  Venue Latitude  Venue Longitude  \
0              Abbey Cafe       51.492258         0.136148   
1                MrBakeme       51.508452        -0.268543   
2       Amigo's Peri Peri       51.508396        -0.274561   
3                  Subway       51.507509        -0.271781   
4  North China Restaurant       51.508251        -0.277435   

         Venue Category  
0                  Café  
1              Creperie  
2  Fast Food Restaurant  
3        Sandwich Place  
4    Chinese Restaurant

Counting/grouping the venues(restaurant info) returned for each Neighborhood/Location

In [79]:
London_venues[['Neighborhood', 'Venue']].groupby('Neighborhood').count()

Venue
Neighborhood                    
Abbey Wood                     1
Acton                         12
Aldgate                      100
Aldwych                       98
Anerley                        4
Angel                         64
Archway                       23
Arnos Grove                    5
Balham                        32
Bankside                      45
Barbican                      50
Barnes                         6
Barnsbury                     12
Battersea                     18
Bayswater                     89
Bedford Park                   7
Belgravia                     27
Bellingham                     4
Belsize Park                  27
Bermondsey                    12
Bethnal Green                 29
Blackfriars                   50
Blackheath                    25
Blackheath Royal Standard      5
Blackwall                      8
Bounds Green                   6
Bow                           11
Bowes Park                     7
Brent Cross                   16
Brixton                       12
...                          ...
Walthamstow                   27
Walthamstow Village            9
Walworth                      20
Wandsworth                    25
Wanstead                      19
Wapping                        9
Well Hall                      4
West Brompton                 15
West Ealing                   19
West Green                     6
West Hackney                  31
West Ham                       4
West Hampstead                25
West Heath                     1
West Hendon                   10
West Kensington               18
West Norwood                  12
Westcombe Park                 5
Westminster                   24
Whetstone                     16
White City                    17
Whitechapel                   25
Willesden                      6
Wimbledon                     50
Winchmore Hill                 4
Wood Green                    26
Woodford                       8
Woodside Park                  3
Woolwich                       1
Wormwood Scrubs                1

[283 rows x 1 columns]

Below code is to find the neighborhood with <b>NO</b> restaurant information recieved from Foursquare API

In [86]:
x = London_venues[['Neighborhood', 'Venue']].groupby('Neighborhood').count().shape[0]
y = df_london.shape[0]
empty_locations = []
if x != y:
    print('Missing data for {0} locations:'.format(y-x))
    # And print them
    for i in range(df_london.shape[0]):
        loc = df_london.iloc[i,0]
        k = 0
        for j in range(London_venues.shape[0]):
            if loc == London_venues.iloc[j,0]:
                k += 1
        if k == 0:
            print(i,loc)
            empty_locations.append(loc)

Missing data for 10 locations:
25 Bloomsbury
30 Brent Park
50 Chinbrook
63 Crossness
69 Dartford
113 Hampstead Garden Suburb
154 Little Ilford
166 Mill Hill


Lets check the unique categories of restuarant information recieved from Foursquare API

In [217]:
print('There are {0} uniques categories.'.format(len(London_venues['Venue Category'].unique())))

There are 126 uniques categories.


By observating the London_venues dataset - it is evident that it has venues inlcuding cafes and bakeries. In this project the focus is more on restaturants. hence ,assigning the dataframe to a new dataframe London_restaurant by filtering out Venue categories containing text "Restaurant"

In [229]:
London_restaurants = London_venues[London_venues['Venue Category'].str.contains("Restaurant")] 
London_restaurants.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
2        Acton               51.50814               -0.273261   
4        Acton               51.50814               -0.273261   
5        Acton               51.50814               -0.273261   
6        Acton               51.50814               -0.273261   
9        Acton               51.50814               -0.273261   

                    Venue  Venue Latitude  Venue Longitude  \
2       Amigo's Peri Peri       51.508396        -0.274561   
4  North China Restaurant       51.508251        -0.277435   
5                  Subway       51.507501        -0.271765   
6                  Ming's       51.507456        -0.272260   
9           Sam's Chicken       51.507193        -0.270431   

         Venue Category  
2  Fast Food Restaurant  
4    Chinese Restaurant  
5            Restaurant  
6    Chinese Restaurant  
9  Fast Food Restaurant

Analysis of each neighborhood - by transforming collected information using the one-hot encoding method.

In [230]:
# one hot encoding
london_onehot = pd.get_dummies(London_restaurants[['Venue Category']], prefix="", prefix_sep="")

# add location column back to dataframe
london_onehot['Neighborhood'] = London_restaurants['Neighborhood'] 

# move location column to the first column
fixed_columns = [london_onehot.columns[-1]] + list(london_onehot.columns[:-1])
london_onehot = london_onehot[fixed_columns]

london_onehot.head()

Neighborhood  Afghan Restaurant  African Restaurant  American Restaurant  \
2        Acton                  0                   0                    0   
4        Acton                  0                   0                    0   
5        Acton                  0                   0                    0   
6        Acton                  0                   0                    0   
9        Acton                  0                   0                    0   

   Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  \
2                 0                       0                 0   
4                 0                       0                 0   
5                 0                       0                 0   
6                 0                       0                 0   
9                 0                       0                 0   

   Australian Restaurant  Austrian Restaurant  Belgian Restaurant  ...  \
2                      0                    0                   0  ...   
4                      0                    0                   0  ...   
5                      0                    0                   0  ...   
6                      0                    0                   0  ...   
9                      0                    0                   0  ...   

   Tapas Restaurant  Thai Restaurant  Turkish Restaurant  Udon Restaurant  \
2                 0                0                   0                0   
4                 0                0                   0                0   
5                 0                0                   0                0   
6                 0                0                   0                0   
9                 0                0                   0                0   

   Vegetarian / Vegan Restaurant  Veneto Restaurant  Vietnamese Restaurant  \
2                              0                  0                      0   
4                              0                  0                      0   
5                              0                  0                      0   
6                              0                  0                      0   
9                              0                  0                      0   

   Xinjiang Restaurant  Yakitori Restaurant  Yoshoku Restaurant  
2                    0                    0                   0  
4                    0                    0                   0  
5                    0                    0                   0  
6                    0                    0                   0  
9                    0                    0                   0  

[5 rows x 89 columns]

In [231]:
london_onehot.shape

(3342, 89)

In [262]:
print('There are {} restaurants in London with {} different style of cuisines.'.format(london_onehot.shape[0],(london_onehot.shape[1]-1)))

There are 3342 restaurants in London with 88 different style of cuisines.


We are now going to group rows by neighborhood and by taking the mean of the frequency of occurrence of each category preparing the dataframe for clustering.



In [233]:
London_grouped = london_onehot.groupby('Neighborhood').mean().reset_index()
London_grouped

Neighborhood  Afghan Restaurant  African Restaurant  \
0                        Acton              0.000            0.000000   
1                      Aldgate              0.000            0.000000   
2                      Aldwych              0.000            0.000000   
3                      Anerley              0.000            0.000000   
4                        Angel              0.025            0.000000   
5                      Archway              0.000            0.000000   
6                  Arnos Grove              0.000            0.000000   
7                       Balham              0.000            0.000000   
8                     Bankside              0.000            0.000000   
9                     Barbican              0.000            0.000000   
10                      Barnes              0.000            0.000000   
11                   Barnsbury              0.000            0.000000   
12                   Battersea              0.000            0.000000   
13                   Bayswater              0.000            0.016949   
14                Bedford Park              0.000            0.000000   
15                   Belgravia              0.000            0.000000   
16                  Bellingham              0.000            0.000000   
17                Belsize Park              0.000            0.000000   
18                  Bermondsey              0.000            0.000000   
19               Bethnal Green              0.000            0.000000   
20                 Blackfriars              0.000            0.000000   
21                  Blackheath              0.000            0.000000   
22   Blackheath Royal Standard              0.000            0.000000   
23                   Blackwall              0.000            0.000000   
24                Bounds Green              0.000            0.000000   
25                         Bow              0.000            0.000000   
26                  Bowes Park              0.000            0.000000   
27                 Brent Cross              0.000            0.000000   
28                     Brixton              0.000            0.000000   
29                    Brockley              0.000            0.000000   
..                         ...                ...                 ...   
236              Upper Norwood              0.000            0.000000   
237          Upper Walthamstow              0.000            0.000000   
238                 Upton Park              0.000            0.000000   
239                   Vauxhall              0.000            0.000000   
240                Walthamstow              0.000            0.000000   
241        Walthamstow Village              0.000            0.000000   
242                   Walworth              0.000            0.000000   
243                 Wandsworth              0.000            0.000000   
244                   Wanstead              0.000            0.000000   
245                    Wapping              0.000            0.000000   
246                  Well Hall              0.000            0.000000   
247              West Brompton              0.000            0.000000   
248                West Ealing              0.000            0.000000   
249                 West Green              0.000            0.000000   
250               West Hackney              0.000            0.000000   
251             West Hampstead              0.000            0.000000   
252                 West Heath              0.000            0.000000   
253                West Hendon              0.000            0.000000   
254            West Kensington              0.000            0.000000   
255               West Norwood              0.000            0.000000   
256             Westcombe Park              0.000            0.000000   
257                Westminster              0.000            0.000000   
258                  Whetstone              0.000            0.000000   
259

In [234]:
London_grouped.shape

(266, 89)

#### Top 5 restaurants for each Neighborhood based on cuisine

In [235]:
num_top_rest = 5

for hood in London_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = London_grouped[London_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_rest))
    print('\n')    
    

----Acton----
                  venue  freq
0  Fast Food Restaurant  0.38
1    Chinese Restaurant  0.25
2   Japanese Restaurant  0.12
3    Turkish Restaurant  0.12
4            Restaurant  0.12


----Aldgate----
                venue  freq
0   Indian Restaurant  0.12
1  Italian Restaurant  0.10
2          Restaurant  0.08
3    Sushi Restaurant  0.08
4     Thai Restaurant  0.07


----Aldwych----
                 venue  freq
0           Restaurant  0.21
1   Italian Restaurant  0.10
2    French Restaurant  0.09
3   English Restaurant  0.07
4  Japanese Restaurant  0.07


----Anerley----
                   venue  freq
0   Fast Food Restaurant   1.0
1      Afghan Restaurant   0.0
2     Kurdish Restaurant   0.0
3       Ramen Restaurant   0.0
4  Portuguese Restaurant   0.0


----Angel----
                venue  freq
0    Sushi Restaurant  0.12
1  Italian Restaurant  0.10
2          Restaurant  0.10
3  Mexican Restaurant  0.05
4   Korean Restaurant  0.05


----Archway----
                 venue

#### Creating a new dataframe with the top 10 restaurants/cuisine based on occurance for each neighborhood

In [264]:
# A function to sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [265]:
#Creating a new dataframe and displaying the top 10 restaurants based on occurance and cuisine for each neighborhood
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = London_grouped['Neighborhood']


for ind in np.arange(London_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(London_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0        Acton  Fast Food Restaurant    Chinese Restaurant   
1      Aldgate     Indian Restaurant    Italian Restaurant   
2      Aldwych            Restaurant    Italian Restaurant   
3      Anerley  Fast Food Restaurant    Yoshoku Restaurant   
4        Angel      Sushi Restaurant    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Restaurant   Japanese Restaurant    Turkish Restaurant   
1      Sushi Restaurant            Restaurant       Thai Restaurant   
2     French Restaurant   Japanese Restaurant    English Restaurant   
3   Yakitori Restaurant  Ethiopian Restaurant    Falafel Restaurant   
4            Restaurant     Korean Restaurant    English Restaurant   

  6th Most Common Venue      7th Most Common Venue  8th Most Common Venue  \
0      Greek Restaurant       Ethiopian Restaurant     Falafel Restaurant   
1   Japanese Restaurant  Middle Eastern Restaurant  Vietnamese Restaurant   
2      Sushi Restaurant          Indian Restaurant     Seafood Restaurant   
3   Filipino Restaurant          French Restaurant      German Restaurant   
4    Mexican Restaurant   Mediterranean Restaurant      Indian Restaurant   

    9th Most Common Venue         10th Most Common Venue  
0     Filipino Restaurant              French Restaurant  
1        Greek Restaurant       Mediterranean Restaurant  
2      Spanish Restaurant              Korean Restaurant  
3  Gluten-free Restaurant               Greek Restaurant  
4       French Restaurant  Vegetarian / Vegan Restaurant

In [266]:
# Creating new dataframe to determine best k value by dropping first column
London_clustering_testing = London_grouped.drop('Neighborhood', 1)

Below code is to find out the optimal value for K in K means cluster

In [261]:
#Below code is to find out the optimal value for K in K means cluster
"""from sklearn.cluster import KMeans 
from sklearn import metrics 
from scipy.spatial.distance import cdist 
import numpy as np 
import matplotlib.pyplot as plt 
import pandas as pd
from sklearn.preprocessing import MinMaxScaler


mms = MinMaxScaler()
mms.fit(London_clustering_testing)
data_transformed = mms.transform(London_clustering_testing)

Sum_of_squared_distances = []
K = range(1,15)
for k in K:
    km = KMeans(n_clusters=k)
    km = km.fit(data_transformed)
    Sum_of_squared_distances.append(km.inertia_)
    
plt.plot(K, Sum_of_squared_distances, 'bx-')
plt.xlabel('k')
plt.ylabel('Sum_of_squared_distances')
plt.title('Elbow Method For Optimal k')
plt.show()

from sklearn.metrics import silhouette_score
import matplotlib.pyplot as plt
%matplotlib inline

def plot(x, y, xlabel, ylabel):
    plt.figure(figsize=(20,10))
    plt.plot(np.arange(2, x), y, 'o-')
    plt.xlabel(xlabel)
    plt.ylabel(ylabel)
    plt.xticks(np.arange(2, x))
    plt.show()
    
indices = []
scores = []
max_range = 20

for kclusters in range(2, max_range) :
    
    # Run k-means clustering
    lct = London_clustering_testing
    kmeans = KMeans(n_clusters = kclusters, init = 'k-means++', random_state = 0).fit_predict(lct)
       # Gets the score for the clustering operation performed
    score = silhouette_score(lct, kmeans)
    
    # Appending the index and score to the respective lists
    indices.append(kclusters)
    scores.append(score)
    

plot(max_range, scores, "No. of clusters", "Silhouette Score")
"""

'from sklearn.cluster import KMeans \nfrom sklearn import metrics \nfrom scipy.spatial.distance import cdist \nimport numpy as np \nimport matplotlib.pyplot as plt \nimport pandas as pd\nfrom sklearn.preprocessing import MinMaxScaler\n\n\nmms = MinMaxScaler()\nmms.fit(London_clustering_testing)\ndata_transformed = mms.transform(London_clustering_testing)\n\nSum_of_squared_distances = []\nK = range(1,15)\nfor k in K:\n    km = KMeans(n_clusters=k)\n    km = km.fit(data_transformed)\n    Sum_of_squared_distances.append(km.inertia_)\n    \nplt.plot(K, Sum_of_squared_distances, \'bx-\')\nplt.xlabel(\'k\')\nplt.ylabel(\'Sum_of_squared_distances\')\nplt.title(\'Elbow Method For Optimal k\')\nplt.show()\n\nfrom sklearn.metrics import silhouette_score\nimport matplotlib.pyplot as plt\n%matplotlib inline\n\ndef plot(x, y, xlabel, ylabel):\n    plt.figure(figsize=(20,10))\n    plt.plot(np.arange(2, x), y, \'o-\')\n    plt.xlabel(xlabel)\n    plt.ylabel(ylabel)\n    plt.xticks(np.arange(2, x))\n 

In [241]:
#opt = np.argmax(scores) + 2 # Finds the optimal value
#opt

#### Clustering neighborhood (based on type of restaurants) using K-means clustering 

Run k-means to cluster the neighborhood into 5 clusters.

In [267]:
# set number of clusters
kclusters = 5

London_grouped_clustering = London_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(London_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 3, 3, 1, 3, 3, 0, 3, 3, 3], dtype=int32)

In [268]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

London_merged = London_restaurants

London_merged = London_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
London_merged.fillna(0)
London_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
2        Acton               51.50814               -0.273261   
4        Acton               51.50814               -0.273261   
5        Acton               51.50814               -0.273261   
6        Acton               51.50814               -0.273261   
9        Acton               51.50814               -0.273261   

                    Venue  Venue Latitude  Venue Longitude  \
2       Amigo's Peri Peri       51.508396        -0.274561   
4  North China Restaurant       51.508251        -0.277435   
5                  Subway       51.507501        -0.271765   
6                  Ming's       51.507456        -0.272260   
9           Sam's Chicken       51.507193        -0.270431   

         Venue Category  Cluster Labels 1st Most Common Venue  \
2  Fast Food Restaurant               1  Fast Food Restaurant   
4    Chinese Restaurant               1  Fast Food Restaurant   
5            Restaurant               1  Fast Food Restaurant   
6    Chinese Restaurant               1  Fast Food Restaurant   
9  Fast Food Restaurant               1  Fast Food Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
2    Chinese Restaurant            Restaurant   Japanese Restaurant   
4    Chinese Restaurant            Restaurant   Japanese Restaurant   
5    Chinese Restaurant            Restaurant   Japanese Restaurant   
6    Chinese Restaurant            Restaurant   Japanese Restaurant   
9    Chinese Restaurant            Restaurant   Japanese Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
2    Turkish Restaurant      Greek Restaurant  Ethiopian Restaurant   
4    Turkish Restaurant      Greek Restaurant  Ethiopian Restaurant   
5    Turkish Restaurant      Greek Restaurant  Ethiopian Restaurant   
6    Turkish Restaurant      Greek Restaurant  Ethiopian Restaurant   
9    Turkish Restaurant      Greek Restaurant  Ethiopian Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
2    Falafel Restaurant   Filipino Restaurant      French Restaurant  
4    Falafel Restaurant   Filipino Restaurant      French Restaurant  
5    Falafel Restaurant   Filipino Restaurant      French Restaurant  
6    Falafel Restaurant   Filipino Restaurant      French Restaurant  
9    Falafel Restaurant   Filipino Restaurant      French Restaurant

Number of venues belonging to each cluster

In [271]:
London_merged['Cluster Labels'].value_counts()

3    2899
1     177
0     120
2      86
4      60
Name: Cluster Labels, dtype: int64

#### Creating map for these cluster for better visualization

In [272]:
# create map
map_clusters = folium.Map(location=[lat_e, long_e], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
count=0
for lat, lon, poi, cluster, vc in zip(London_merged['Venue Latitude'], London_merged['Venue Longitude'], London_merged['Venue'], London_merged['Cluster Labels'], London_merged['Venue Category']):
    label = folium.Popup(str(poi) +' (' +str(vc) + ') ['+ str(cluster)+']', parse_html=True)

    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.6).add_to(map_clusters)
    count += 1
map_clusters

### 4. Results

Lets examine each of these clusters to find out the most common and least common restaurant types for the recommendation system.

#### Cluster 1

In [247]:
c1 = London_merged.loc[London_merged['Cluster Labels'] ==0, London_merged.columns[[0]+list(range(5, London_merged.shape[1]))]]
c1.drop_duplicates()

Neighborhood  Venue Longitude                 Venue Category  \
302      Arnos Grove        -0.134875             Turkish Restaurant   
305      Arnos Grove        -0.134448              Indian Restaurant   
306      Arnos Grove        -0.128742             Chinese Restaurant   
806         Brockley        -0.036473               Malay Restaurant   
813         Brockley        -0.034321             Chinese Restaurant   
814         Brockley        -0.037258           Fast Food Restaurant   
816         Brockley        -0.037983             Chinese Restaurant   
817         Brockley        -0.037711             Chinese Restaurant   
1698    Crofton Park        -0.036473               Malay Restaurant   
1701    Crofton Park        -0.037258           Fast Food Restaurant   
1703    Crofton Park        -0.037711             Chinese Restaurant   
1706    Crofton Park        -0.037983             Chinese Restaurant   
1749  Crystal Palace        -0.073229             Chinese Restaurant   
1854    Denmark Hill        -0.093227          Portuguese Restaurant   
1855    Denmark Hill        -0.092910          Vietnamese Restaurant   
1857    Denmark Hill        -0.092912             Chinese Restaurant   
1858    Denmark Hill        -0.092740            Lebanese Restaurant   
1859    Denmark Hill        -0.093061              Indian Restaurant   
2301     Forest Hill        -0.053865          Vietnamese Restaurant   
2304     Forest Hill        -0.056089             Chinese Restaurant   
2305     Forest Hill        -0.056089              Indian Restaurant   
2314   Friern Barnet        -0.158121             Italian Restaurant   
2316   Friern Barnet        -0.163083             Chinese Restaurant   
2459      Grove Park        -0.337334             Chinese Restaurant   
2460      Grove Park        -0.337830           Fast Food Restaurant   
2462      Grove Park        -0.337967           Fast Food Restaurant   
2463      Grove Park        -0.337678                     Restaurant   
2465      Grove Park         0.021171              Indian Restaurant   
2468      Grove Park         0.021822             Chinese Restaurant   
2469      Grove Park         0.021227              Indian Restaurant   
...              ...              ...                            ...   
4934       Southgate        -0.126004             Chinese Restaurant   
4935       Southgate        -0.126613             Chinese Restaurant   
5278         Stepney        -0.047662                Thai Restaurant   
5280         Stepney        -0.046892             Turkish Restaurant   
5281         Stepney        -0.049078             Chinese Restaurant   
5285         Stepney        -0.049514              Indian Restaurant   
5286         Stepney        -0.047216           Fast Food Restaurant   
5287         Stepney        -0.047370           Fast Food Restaurant   
5288         Stepney        -0.047060             Chinese Restaurant   
5290         Stepney        -0.048276             Mexican Restaurant   
5399       Streatham        -0.129478  Vegetarian / Vegan Restaurant   
5402       Streatham        -0.131076             Chinese Restaurant   
5405       Streatham        -0.128161               Sushi Restaurant   
5406       Streatham        -0.130535          Vietnamese Restaurant   
5407       Streatham        -0.129618           Fast Food Restaurant   
5408       Streatham        -0.129052             Chinese Restaurant   
5409       Streatham        -0.130596          Vietnamese Restaurant   
5410       Streatham        -0.129493              Polish Restaurant   
5688   Upper Clapton        -0.058265             Turkish Restaurant   
5691   Upper Clapton        -0.059435             Chinese Restaurant   
5693   Upper Clapton        -0.061966             Chinese Restaurant   
5857       Well Hall         0.049384                     Restaurant   
5859       Well Hall         0.050845             Chinese Restaurant   
5860       Well Hall         0.051952           

In [248]:
cluster_1 = London_merged.loc[London_merged['Cluster Labels'] == 0, London_merged.columns[[0] + list(range(5, London_merged.shape[1]))]]
cluster_1.describe(include='all')

Neighborhood  Venue Longitude      Venue Category  Cluster Labels  \
count           120       120.000000                 120           120.0   
unique           26              NaN                  27             NaN   
top       New Cross              NaN  Chinese Restaurant             NaN   
freq             14              NaN                  43             NaN   
mean            NaN        -0.071297                 NaN             0.0   
std             NaN         0.081099                 NaN             0.0   
min             NaN        -0.337967                 NaN             0.0   
25%             NaN        -0.123175                 NaN             0.0   
50%             NaN        -0.045557                 NaN             0.0   
75%             NaN        -0.036175                 NaN             0.0   
max             NaN         0.089511                 NaN             0.0   

       1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
count                    120                   120                   120   
unique                    10                    10                    13   
top       Chinese Restaurant    Chinese Restaurant     Indian Restaurant   
freq                      60                    32                    22   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
count                    120                   120                   120   
unique                    12                    11                    10   
top       Yoshoku Restaurant      Halal Restaurant    Falafel Restaurant   
freq                      21                    18                    30   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
count                    120                   120                   120   
unique                     9                     9                     8   
top     Fast Food Restaurant    Falafel Restaurant  Fast Food Restaurant   
freq                      29                    27                    27   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       10th Most Common Venue  
count                     120  
unique                      8  
top       Filipino Restaurant  
freq                       27  
mean                      NaN  
std                       NaN  
min                       NaN  
25%                       NaN  
50%                       NaN  
75%                       NaN  
max

#### Cluster 2

In [282]:
c2 = London_merged.loc[London_merged['Cluster Labels'] == 1, London_merged.columns[[0]+list(range(5, London_merged.shape[1]))]]
c2.drop_duplicates()

Neighborhood  Venue Longitude            Venue Category  \
2                         Acton        -0.274561      Fast Food Restaurant   
4                         Acton        -0.277435        Chinese Restaurant   
5                         Acton        -0.271765                Restaurant   
6                         Acton        -0.272260        Chinese Restaurant   
9                         Acton        -0.270431      Fast Food Restaurant   
10                        Acton        -0.272239        Turkish Restaurant   
11                        Acton        -0.269494       Japanese Restaurant   
12                        Acton        -0.270255      Fast Food Restaurant   
212                     Anerley        -0.059266      Fast Food Restaurant   
740   Blackheath Royal Standard         0.021685      Fast Food Restaurant   
741   Blackheath Royal Standard         0.019469        Chinese Restaurant   
778                 Brent Cross        -0.224028     Portuguese Restaurant   
785                 Brent Cross        -0.224063          Asian Restaurant   
786                 Brent Cross        -0.224110          Sushi Restaurant   
790                 Brent Cross        -0.224379      Fast Food Restaurant   
791                 Brent Cross        -0.224034      Fast Food Restaurant   
792                 Brent Cross        -0.223742      Fast Food Restaurant   
1187                   Charlton         0.032703           Thai Restaurant   
1189                   Charlton         0.037656      Fast Food Restaurant   
1563                  Colindale        -0.242935        Chinese Restaurant   
1564                  Colindale        -0.249954      Fast Food Restaurant   
1568                  Colindale        -0.242829                Restaurant   
1682                Cricklewood        -0.213378        Italian Restaurant   
1685                Cricklewood        -0.212900         Afghan Restaurant   
1686                Cricklewood        -0.214386      Fast Food Restaurant   
1687                Cricklewood        -0.215005      Fast Food Restaurant   
1690                Cricklewood        -0.215664      Fast Food Restaurant   
1691                Cricklewood        -0.214410      Fast Food Restaurant   
1692                Cricklewood        -0.214493      Fast Food Restaurant   
1694                Cricklewood        -0.214298          Asian Restaurant   
...                         ...              ...                       ...   
5785                   Walworth        -0.091887       Lebanese Restaurant   
5789                   Walworth        -0.096059           Thai Restaurant   
5791                   Walworth        -0.094796          Asian Restaurant   
5792                   Walworth        -0.096388      Caribbean Restaurant   
5795                   Walworth        -0.096079      Fast Food Restaurant   
5796                   Walworth        -0.096597      Fast Food Restaurant   
5799                   Walworth        -0.095336      Fast Food Restaurant   
5800                   Walworth        -0.095062        English Restaurant   
5849                    Wapping        -0.058122         Indian Restaurant   
5850                    Wapping        -0.058365        Italian Restaurant   
5851                    Wapping        -0.054023        Chinese Restaurant   
5852                    Wapping        -0.052521        Italian Restaurant   
5854                    Wapping        -0.057871      Fast Food Restaurant   
5856                    Wapping        -0.060629      Fast Food Restaurant   
6149                 Wood Green        -0.108992  Mediterranean Restaurant   
6150                 Wood Green        -0.109100  Mediterranean Restaurant   
6151                 Wood Green        -0.108921        Turkish Restaurant   
6152                 Wood Green        -0.108750     Portuguese Restaurant   
6153                 Wood Green        -0.108899        Turkish Restaurant   
6155                 Wood Green        -0

In [250]:
cluster_1 = London_merged.loc[London_merged['Cluster Labels'] == 1, London_merged.columns[[0] + list(range(5, London_merged.shape[1]))]]
cluster_1.describe(include='all')

Neighborhood  Venue Longitude        Venue Category  Cluster Labels  \
count           177       177.000000                   177           177.0   
unique           31              NaN                    27             NaN   
top      Wood Green              NaN  Fast Food Restaurant             NaN   
freq             16              NaN                    81             NaN   
mean            NaN        -0.107754                   NaN             1.0   
std             NaN         0.098638                   NaN             0.0   
min             NaN        -0.339465                   NaN             1.0   
25%             NaN        -0.213378                   NaN             1.0   
50%             NaN        -0.095468                   NaN             1.0   
75%             NaN        -0.043488                   NaN             1.0   
max             NaN         0.058403                   NaN             1.0   

       1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
count                    177                   177                   177   
unique                     2                    19                    14   
top     Fast Food Restaurant    Italian Restaurant            Restaurant   
freq                     165                    22                    42   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       4th Most Common Venue 5th Most Common Venue  6th Most Common Venue  \
count                    177                   177                    177   
unique                    15                    13                     12   
top       Italian Restaurant    Chinese Restaurant  Portuguese Restaurant   
freq                      27                    25                     37   
mean                     NaN                   NaN                    NaN   
std                      NaN                   NaN                    NaN   
min                      NaN                   NaN                    NaN   
25%                      NaN                   NaN                    NaN   
50%                      NaN                   NaN                    NaN   
75%                      NaN                   NaN                    NaN   
max                      NaN                   NaN                    NaN   

       7th Most Common Venue   8th Most Common Venue 9th Most Common Venue  \
count                    177                     177                   177   
unique                    12                       7                     7   
top      Filipino Restaurant  Gluten-free Restaurant   Filipino Restaurant   
freq                      31                      38                    40   
mean                     NaN                     NaN                   NaN   
std                      NaN                     NaN                   NaN   
min                      NaN                     NaN                   NaN   
25%                      NaN                     NaN                   NaN   
50%                      NaN                     NaN                   NaN   
75%                      NaN                     NaN                   NaN   
max                      NaN                     NaN                   NaN   

       10th Most Common Venue  
count                     177  
unique                      7  
top         French Restaurant  
freq                       40  
mean                      NaN  
std                       NaN  
min                       NaN  
25%                       NaN  
50%    

#### Cluster 3

In [252]:
c2 = London_merged.loc[London_merged['Cluster Labels'] == 2, London_merged.columns[[0]+list(range(5, London_merged.shape[1]))]]
c2.drop_duplicates()

Neighborhood  Venue Longitude               Venue Category  \
755    Bounds Green        -0.124613    Middle Eastern Restaurant   
756    Bounds Green        -0.127042            Indian Restaurant   
772      Bowes Park        -0.116601             Greek Restaurant   
775      Bowes Park        -0.124613    Middle Eastern Restaurant   
776      Bowes Park        -0.127042            Indian Restaurant   
793         Brixton        -0.113276   Modern European Restaurant   
795         Brixton        -0.116038             Tapas Restaurant   
797         Brixton        -0.116558         Caribbean Restaurant   
798         Brixton        -0.119421            Indian Restaurant   
799         Brixton        -0.113471            Indian Restaurant   
804         Brixton        -0.113651         Fast Food Restaurant   
1582   Colney Hatch        -0.147811           Chinese Restaurant   
1584   Colney Hatch        -0.148697            Indian Restaurant   
1585   Colney Hatch        -0.147519            Indian Restaurant   
1586   Colney Hatch        -0.147118  Eastern European Restaurant   
1755    Cubitt Town        -0.006707            Indian Restaurant   
1756    Cubitt Town        -0.009779            Indian Restaurant   
2021       East Ham         0.050299            Indian Restaurant   
2022       East Ham         0.050633            Indian Restaurant   
2023       East Ham         0.050107            Indian Restaurant   
2024       East Ham         0.049992            Indian Restaurant   
2025       East Ham         0.051360            Indian Restaurant   
2028       East Ham         0.050528         Fast Food Restaurant   
2029       East Ham         0.051187            Indian Restaurant   
2030       East Ham         0.051440         Fast Food Restaurant   
2031       East Ham         0.051101            Indian Restaurant   
2032       East Ham         0.051147            Indian Restaurant   
2033       East Ham         0.050662            Indian Restaurant   
2034       East Ham         0.051946         Fast Food Restaurant   
2035       East Ham         0.056761            Indian Restaurant   
...             ...              ...                          ...   
3638       Millwall        -0.022929           Chinese Restaurant   
3639       Millwall        -0.018530    Middle Eastern Restaurant   
3640       Millwall        -0.018536            Indian Restaurant   
3787  New Southgate        -0.143501         Fast Food Restaurant   
3789  New Southgate        -0.149623            Indian Restaurant   
3818      Nine Elms        -0.135371                   Restaurant   
3821      Nine Elms        -0.137108            Indian Restaurant   
3937         Osidge        -0.143475          American Restaurant   
3938         Osidge        -0.142938             Greek Restaurant   
3939         Osidge        -0.143371            Indian Restaurant   
3941         Osidge        -0.143379            Indian Restaurant   
3942         Osidge        -0.138112         Fast Food Restaurant   
3943         Osidge        -0.149610            Indian Restaurant   
4874  South Norwood        -0.076470             Asian Restaurant   
4877  South Norwood        -0.073085            Indian Restaurant   
4916       Southend        -0.021504            Indian Restaurant   
5606     Totteridge        -0.205457            Indian Restaurant   
5721     Upton Park         0.032979            Indian Restaurant   
5725     Upton Park         0.035213         Fast Food Restaurant   
5726     Upton Park         0.033292            Indian Restaurant   
5877    West Ealing        -0.315841           Persian Restaurant   
5878    West Ealing        -0.314637           Persian Restaurant   
5879    West Ealing        -0.320906             Doner Restaurant   
5880    West Ealing        -0.321910            Indian Restaurant   
5882    West Ealing        -0.314747             Greek Restaurant   
5884    West Ealing        -0.317962           Turkish Restaurant   
5887 

In [253]:
cluster_1 = London_merged.loc[London_merged['Cluster Labels'] == 2, London_merged.columns[[0] + list(range(5, London_merged.shape[1]))]]
cluster_1.describe(include='all')

Neighborhood  Venue Longitude     Venue Category  Cluster Labels  \
count            86        86.000000                 86            86.0   
unique           24              NaN                 21             NaN   
top        East Ham              NaN  Indian Restaurant             NaN   
freq             13              NaN                 46             NaN   
mean            NaN        -0.073356                NaN             2.0   
std             NaN         0.115802                NaN             0.0   
min             NaN        -0.321910                NaN             2.0   
25%             NaN        -0.143377                NaN             2.0   
50%             NaN        -0.074777                NaN             2.0   
75%             NaN         0.034733                NaN             2.0   
max             NaN         0.127674                NaN             2.0   

       1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
count                     86                    86                    86   
unique                     6                     9                     8   
top        Indian Restaurant  Fast Food Restaurant    Yoshoku Restaurant   
freq                      72                    22                    28   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
count                     86                    86                    86   
unique                    11                     7                     7   
top         Halal Restaurant  Ethiopian Restaurant    Falafel Restaurant   
freq                      26                    28                    37   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
count                     86                    86                    86   
unique                     6                     5                     4   
top      Filipino Restaurant     French Restaurant     German Restaurant   
freq                      31                    31                    31   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

        10th Most Common Venue  
count                       86  
unique                       4  
top     Gluten-free Restaurant  
freq                        31  
mean                       NaN  
std                        NaN  
min                        NaN  
25%                        NaN  
50%                        NaN  
75%                        NaN  
max 

#### Cluster 4

In [254]:
c2 = London_merged.loc[London_merged['Cluster Labels'] == 3, London_merged.columns[[0]+list(range(5, London_merged.shape[1]))]]
c2.drop_duplicates()

Neighborhood  Venue Longitude                 Venue Category  \
15           Aldgate        -0.079079            Japanese Restaurant   
16           Aldgate        -0.075434             Italian Restaurant   
17           Aldgate        -0.070606                     Restaurant   
18           Aldgate        -0.075438         Argentinian Restaurant   
20           Aldgate        -0.076932            Szechuan Restaurant   
21           Aldgate        -0.076465                     Restaurant   
23           Aldgate        -0.077195              Indian Restaurant   
25           Aldgate        -0.080360                     Restaurant   
26           Aldgate        -0.081169               Sushi Restaurant   
27           Aldgate        -0.075626                Thai Restaurant   
29           Aldgate        -0.076195          Vietnamese Restaurant   
30           Aldgate        -0.077177       Mediterranean Restaurant   
31           Aldgate        -0.074732              Indian Restaurant   
33           Aldgate        -0.068825      Middle Eastern Restaurant   
36           Aldgate        -0.076886             Italian Restaurant   
37           Aldgate        -0.078564      Middle Eastern Restaurant   
38           Aldgate        -0.072967               Asian Restaurant   
39           Aldgate        -0.079230              Indian Restaurant   
40           Aldgate        -0.074570          Vietnamese Restaurant   
41           Aldgate        -0.073453               Sushi Restaurant   
42           Aldgate        -0.079027              French Restaurant   
43           Aldgate        -0.077992               Asian Restaurant   
44           Aldgate        -0.080238             English Restaurant   
45           Aldgate        -0.073943      Middle Eastern Restaurant   
46           Aldgate        -0.076552            Empanada Restaurant   
47           Aldgate        -0.073249             Chinese Restaurant   
48           Aldgate        -0.070137             Falafel Restaurant   
49           Aldgate        -0.073547                Thai Restaurant   
51           Aldgate        -0.079587                     Restaurant   
53           Aldgate        -0.078152       Mediterranean Restaurant   
...              ...              ...                            ...   
6100       Wimbledon        -0.201979             Italian Restaurant   
6101       Wimbledon        -0.205293              Indian Restaurant   
6103       Wimbledon        -0.204652             Mexican Restaurant   
6104       Wimbledon        -0.203459           Brazilian Restaurant   
6105       Wimbledon        -0.205120             English Restaurant   
6106       Wimbledon        -0.201961          Portuguese Restaurant   
6109       Wimbledon        -0.205112               Sushi Restaurant   
6110       Wimbledon        -0.211218  Vegetarian / Vegan Restaurant   
6111       Wimbledon        -0.205566              Indian Restaurant   
6112       Wimbledon        -0.208771          Vietnamese Restaurant   
6114       Wimbledon        -0.201557                     Restaurant   
6117       Wimbledon        -0.207972                     Restaurant   
6119       Wimbledon        -0.206594               Sushi Restaurant   
6120       Wimbledon        -0.205852               Sushi Restaurant   
6122       Wimbledon        -0.202613                Thai Restaurant   
6124       Wimbledon        -0.208710             Italian Restaurant   
6127       Wimbledon        -0.207067           Fast Food Restaurant   
6128       Wimbledon        -0.205011             Italian Restaurant   
6129       Wimbledon        -0.208676             Italian Restaurant   
6133       Wimbledon        -0.208188                Thai Restaurant   
6136       Wimbledon        -0.202646               Asian Restaurant   
6139       Wimbledon        -0.202305           Fast Food Restaurant   
6141       Wimbledon        -0.202352           Fast Food Restaurant   
6142       Wimbledon        -0.200600        Nor

In [255]:
cluster_1 = London_merged.loc[London_merged['Cluster Labels'] == 3, London_merged.columns[[0] + list(range(5, London_merged.shape[1]))]]
cluster_1.describe(include='all')

Neighborhood  Venue Longitude      Venue Category  Cluster Labels  \
count          2899      2899.000000                2899          2899.0   
unique          175              NaN                  87             NaN   
top         Aldgate              NaN  Italian Restaurant             NaN   
freq             72              NaN                 376             NaN   
mean            NaN        -0.129506                 NaN             3.0   
std             NaN         0.063537                 NaN             0.0   
min             NaN        -0.308454                 NaN             3.0   
25%             NaN        -0.174251                 NaN             3.0   
50%             NaN        -0.125022                 NaN             3.0   
75%             NaN        -0.098466                 NaN             3.0   
max             NaN         0.072767                 NaN             3.0   

       1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
count                   2899                  2899                  2899   
unique                    28                    31                    39   
top       Italian Restaurant    Italian Restaurant            Restaurant   
freq                    1188                   727                   352   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
count                   2899                  2899                  2899   
unique                    40                    39                    44   
top        Indian Restaurant            Restaurant      Sushi Restaurant   
freq                     404                   308                   227   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
count                   2899                  2899                  2899   
unique                    50                    44                    47   
top          Thai Restaurant    Seafood Restaurant    Falafel Restaurant   
freq                     203                   262                   168   
mean                     NaN                   NaN                   NaN   
std                      NaN                   NaN                   NaN   
min                      NaN                   NaN                   NaN   
25%                      NaN                   NaN                   NaN   
50%                      NaN                   NaN                   NaN   
75%                      NaN                   NaN                   NaN   
max                      NaN                   NaN                   NaN   

       10th Most Common Venue  
count                    2899  
unique                     52  
top        Mexican Restaurant  
freq                      220  
mean                      NaN  
std                       NaN  
min                       NaN  
25%                       NaN  
50%                       NaN  
75%                       NaN  
max

#### Cluster 5

In [259]:
c2 = London_merged.loc[London_merged['Cluster Labels'] == 4, London_merged.columns[[0]+list(range(5, London_merged.shape[1]))]]
c2.drop_duplicates()

Neighborhood  Venue Longitude             Venue Category  \
593          Bellingham        -0.017902         Turkish Restaurant   
594          Bellingham        -0.015619       Fast Food Restaurant   
759                 Bow        -0.026779         Turkish Restaurant   
765                 Bow        -0.027413       Fast Food Restaurant   
769                 Bow        -0.029928         Chinese Restaurant   
847      Brunswick Park        -0.153290         Turkish Restaurant   
1066       Canning Town         0.009132         Turkish Restaurant   
1067       Canning Town         0.010700         Italian Restaurant   
1068       Canning Town         0.012059       Fast Food Restaurant   
1070       Canning Town         0.008953         Turkish Restaurant   
1072       Canning Town         0.011984                 Restaurant   
2686          Harringay        -0.098950         Turkish Restaurant   
2687          Harringay        -0.099009         Turkish Restaurant   
2688          Harringay        -0.098844         Turkish Restaurant   
2689          Harringay        -0.099032         Turkish Restaurant   
2690          Harringay        -0.104307           Tapas Restaurant   
2692          Harringay        -0.098790         Turkish Restaurant   
2694          Harringay        -0.099099         Turkish Restaurant   
2695          Harringay        -0.099004         Turkish Restaurant   
2696          Harringay        -0.099116   Mediterranean Restaurant   
2697          Harringay        -0.099064         Turkish Restaurant   
2700          Harringay        -0.098781         Turkish Restaurant   
2703          Harringay        -0.098633                 Restaurant   
2704          Harringay        -0.099052       Fast Food Restaurant   
2705          Harringay        -0.098487                 Restaurant   
3922           Old Ford        -0.026779         Turkish Restaurant   
3925           Old Ford        -0.027413       Fast Food Restaurant   
4405        Shacklewell        -0.070647   Mediterranean Restaurant   
4406        Shacklewell        -0.074303         Turkish Restaurant   
4409        Shacklewell        -0.075033                 Restaurant   
4410        Shacklewell        -0.074903       Caribbean Restaurant   
4411        Shacklewell        -0.075044           Cuban Restaurant   
4412        Shacklewell        -0.075252         Turkish Restaurant   
4413        Shacklewell        -0.074955           Kebab Restaurant   
4415        Shacklewell        -0.075443         Turkish Restaurant   
4417        Shacklewell        -0.074744  Middle Eastern Restaurant   
4420        Shacklewell        -0.074864         Mexican Restaurant   
4421        Shacklewell        -0.075026         Turkish Restaurant   
4422        Shacklewell        -0.075265   Mediterranean Restaurant   
4423        Shacklewell        -0.075389         Turkish Restaurant   
4424        Shacklewell        -0.075231         Turkish Restaurant   
4426        Shacklewell        -0.075172   Mediterranean Restaurant   
4428        Shacklewell        -0.074987         Falafel Restaurant   
4429        Shacklewell        -0.075209           Kebab Restaurant   
4430        Shacklewell        -0.075048         Turkish Restaurant   
4432        Shacklewell        -0.075226         Turkish Restaurant   
4433        Shacklewell        -0.075246         Mexican Restaurant   
4434        Shacklewell        -0.074864      Portuguese Restaurant   
4435        Shacklewell        -0.065353                 Restaurant   
5588    Tottenham Green        -0.071591           Tapas Restaurant   
5590    Tottenham Green        -0.069925         Turkish Restaurant   
5591    Tottenham Green        -0.071597         Turkish Restaurant   
5597    Tottenham Green        -0.066791       Fast Food Restaurant   
5598    Tottenham Green        -0.066591         Chinese Restaurant   
5717  Upper Walthamstow        -0.003962         Turkish Restaurant   
5718  Upper Walthamstow        -0.0

In [260]:
cluster_1 = London_merged.loc[London_merged['Cluster Labels'] == 4, London_merged.columns[[0] + list(range(5, London_merged.shape[1]))]]
cluster_1.describe(include='all')

Neighborhood  Venue Longitude      Venue Category  Cluster Labels  \
count            60        60.000000                  60            60.0   
unique           10              NaN                  15             NaN   
top     Shacklewell              NaN  Turkish Restaurant             NaN   
freq             22              NaN                  29             NaN   
mean            NaN        -0.065453                 NaN             4.0   
std             NaN         0.036789                 NaN             0.0   
min             NaN        -0.153290                 NaN             4.0   
25%             NaN        -0.095770                 NaN             4.0   
50%             NaN        -0.075029                 NaN             4.0   
75%             NaN        -0.056497                 NaN             4.0   
max             NaN         0.012059                 NaN             4.0   

       1st Most Common Venue     2nd Most Common Venue 3rd Most Common Venue  \
count                     60                        60                    60   
unique                     2                         6                     6   
top       Turkish Restaurant  Mediterranean Restaurant      Kebab Restaurant   
freq                      53                        22                    22   
mean                     NaN                       NaN                   NaN   
std                      NaN                       NaN                   NaN   
min                      NaN                       NaN                   NaN   
25%                      NaN                       NaN                   NaN   
50%                      NaN                       NaN                   NaN   
75%                      NaN                       NaN                   NaN   
max                      NaN                       NaN                   NaN   

       4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
count                     60                    60                         60   
unique                     6                     7                          7   
top               Restaurant    Mexican Restaurant  Middle Eastern Restaurant   
freq                      22                    22                         22   
mean                     NaN                   NaN                        NaN   
std                      NaN                   NaN                        NaN   
min                      NaN                   NaN                        NaN   
25%                      NaN                   NaN                        NaN   
50%                      NaN                   NaN                        NaN   
75%                      NaN                   NaN                        NaN   
max                      NaN                   NaN                        NaN   

        7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
count                      60                    60                    60   
unique                      6                     4                     5   
top     Portuguese Restaurant    Falafel Restaurant      Cuban Restaurant   
freq                       22                    32                    22   
mean                      NaN                   NaN                   NaN   
std                       NaN                   NaN                   NaN   
min                       NaN                   NaN                   NaN   
25%                       NaN                   NaN                   NaN   
50%                       NaN                   NaN                   NaN   
75%                       NaN                   NaN                   NaN   
max                       NaN                   NaN                   NaN   

       10th Most Common Venue  
count                      60  
unique                      5  
top      Caribbean Restaurant  
freq                       22  
mean                      NaN  
std                       NaN  
min        

#### Result Summary 

<table style="width:50%">
<tr>
<th>Cluster</th>
<th>Most Common Restaurant</th>
<th>Least Common Restaurant</th>
</tr>
<tr>
<td>1</td>
<td>Chinese Restaurant</td>
<td>Filipino Restaurant</td>
</tr>
<tr>
<td>2</td>
<td>Fast Food Restaurant  </td>
<td>French Restaurant</td>
</tr>
<tr>
<td>3</td>
<td>Indian Restaurant</td>
<td>Gluten-free Restaurant</td>
</tr>
<tr>
<td>4</td>
<td>Italian Restaurant</td>
<td>Mexican Restaurant</td>
</tr>
<tr>
<td>5</td>
<td>Turkish Restaurant</td>
<td>Caribbean Restaurant</td>
</tr>
</table>

### 5.  Discussion

The analysis can be summarized to say – the safest option to choose the restaurant type for a particular locality is by looking at the least common type. Opening a new Indian restaurant in a street with dozens of Indian dining place makes no sense. Looking at the competition, this will be a risky investment.  However, while choosing the least popular restaurant is also uncertain, given the demand and popularity for that type is food is less in that area. Hence the analysis can be made better by including the analysis of population and demography. The analysis is limited to 10 common venues to eliminate the risk of opening a business with no prospect in a location

Stakeholder can 
* Either choose a location from the cluster and this model can advise what would be the best cuisine to opt for in the locality <btr>
* Or choose a gastronomy , and we can check the model to find out the best suited cluster/locality for that type

### 6. Conclusion

The analysis is performed to find out the most promising type of restaurant and suitable location to start the business.  The data is collected from Wikipedia , geospatial library and foursquare API. The method used is K-means clustering to group the similar neighbourhood on the basis of frequency of certain cuisine types.  Undoubtedly the model can be improved by collecting more information around the neighbourhood population(/demography) , restaurant menu and ratings to come up with better recommendation